# CRI iAtlas notebooks

## Analyze outcome data in Immune Checkpoint Inhibition (ICI) datasets using Cox proportional hazard models.

Repo: https://github.com/CRI-iAtlas/iatlas-notebooks/ 

Notebook: ici_hazard_ratio.ipynb 

Date: September 19, 2022 

Author: Carolina Heimann

---

notebook repo: https://github.com/CRI-iAtlas/iatlas-notebooks

landing page: https://www.cri-iatlas.org/

portal: https://isb-cgc.shinyapps.io/iatlas/

email: support@cri-iatlas.org

---

Welcome to the CRI iAtlas notebooks. With these notebooks you'll be able to recreate many of our figures and modules found in the web portal, but with your own data or configuration. In this case, you will be able to reproduce the workflow implemented in the ICI Hazard Ratio module to use Cox porportional hazard models to analyze outcome data in Immune Checkpoint Inhibition datasets.

This is a jupyter notebook running R. The fastest way to get started is to open the notebook using Jupyter lab in MyBinder, it's free and works great.

If you want to run this on your local environment, you'll need Jupyter and an R kernel to use it.<br>
See [this conda guide](https://docs.anaconda.com/anaconda/navigator/tutorials/r-lang/) or [this datacamp guide](https://www.datacamp.com/community/blog/jupyter-notebook-r) to get started.<br>

## Getting started

In [1]:
# We have a few libraries to install.
try({
    packages = c("magrittr", "dplyr", "tidyr", "plotly", "survival", "dplyr", "iatlasGraphQLClient")

    sapply(packages, function(x) {
      if (!require(x,character.only = TRUE))
        install.packages(x)
        suppressPackageStartupMessages(library(x,character.only = TRUE))
    })

    # and our iatlas package from github
    if (!require(iatlas.modules)) {
      devtools::install_github("CRI-iAtlas/iatlas.modules")
      suppressPackageStartupMessages(library(iatlas.modules))
    }},
    silent=TRUE 
)

Loading required package: magrittr

Loading required package: dplyr


Attaching package: ‘dplyr’


The following objects are masked from ‘package:stats’:

    filter, lag


The following objects are masked from ‘package:base’:

    intersect, setdiff, setequal, union


Loading required package: tidyr


Attaching package: ‘tidyr’


The following object is masked from ‘package:magrittr’:

    extract


Loading required package: plotly

Loading required package: ggplot2


Attaching package: ‘plotly’


The following object is masked from ‘package:ggplot2’:

    last_plot


The following object is masked from ‘package:stats’:

    filter


The following object is masked from ‘package:graphics’:

    layout


Loading required package: survival

Loading required package: arrow


Attaching package: ‘arrow’


The following object is masked from ‘package:plotly’:

    schema


The following object is masked from ‘package:magrittr’:

    is_in


The following object is masked from ‘package:utils’

# Exploring the available ICI datasets and features


**If this is your first time dealing with the ICI data in iAtlas**, we recommend checking the overview of the available ICI datasets and features detailed in the [Exploring the Immune Checkpoint Inhibition data available in iAtlas.](./ici_query_iatlas_data.ipynb) notebook. 



# Selection of parameters

We will use the following features:

- Datasets from SKCM studies: Gide 2019 - SKCM, PD-1 +/- CTLA4, Hugo 2016 - SKCM, PD-1, Liu 2019 - SKCM, PD-1, Riaz 2017 - SKCM, PD-1, Van Allen 2015 - SKCM, CTLA-4

- Survival Endpoint: Overall Survival

- Predictors of response: IMPRES (Auslander et al, 2018), IPRES (Vincent lab analysis of Hugo et al data, unpublished), Cytolytic Score (Roufas et al, 2018), CTLA4/Th1 (Nishimura, 2004; Bindea et al., 2013)


In [18]:
datasets  <- c("Gide_Cell_2019",
              "HugoLo_IPRES_2016",
              "Liu_NatMed_2019",
              "Riaz_Nivolumab_2017",
              "VanAllen_antiCTLA4_2015")

survival_endpoint  <-  c("OS", "OS_time")

features <- c(
                "IMPRES", 
                "Vincent_IPRES_NonResponder", 
                "Cytolytic_Score", 
                "BIOCARTA_CTLA4_V_Bindea_Th1_Cells"
                )

# Querying the database

As a first step, we will get all samples from the datasets of interest that were collected pre ICI treatment and then get the selected immune features and survival endpoint.

In [16]:
samples_pre <- iatlasGraphQLClient::query_dataset_samples(datasets = datasets) %>% #get samples id for the ICI datasets
  dplyr::inner_join(
    iatlasGraphQLClient::query_tag_samples_parents(
      tags = c("pre_sample_treatment")),
    by = "sample_name") %>%
  dplyr::inner_join(iatlasGraphQLClient::query_feature_values(features = c(survival_endpoint, features)),
                            by = c("sample_name" = "sample")) %>%
  dplyr::select(sample_name, dataset_name, dataset_display, feature_name, feature_value) %>%
  tidyr::pivot_wider(., names_from = feature_name, values_from = feature_value, values_fill = NA)

head(samples_pre)

sample_name                dataset_name   dataset_display                 
1 Gide_Cell_2019-iP47-ar-921 Gide_Cell_2019 Gide 2019 - SKCM, PD-1 +/- CTLA4
2 Gide_Cell_2019-PD47-ar-964 Gide_Cell_2019 Gide 2019 - SKCM, PD-1 +/- CTLA4
3 Gide_Cell_2019-iP49-ar-922 Gide_Cell_2019 Gide 2019 - SKCM, PD-1 +/- CTLA4
4 Gide_Cell_2019-iP44-ar-918 Gide_Cell_2019 Gide 2019 - SKCM, PD-1 +/- CTLA4
5 Gide_Cell_2019-PD08-ar-565 Gide_Cell_2019 Gide 2019 - SKCM, PD-1 +/- CTLA4
6 Gide_Cell_2019-PD42-ar-959 Gide_Cell_2019 Gide 2019 - SKCM, PD-1 +/- CTLA4
  BIOCARTA_CTLA4_V_Bindea_Th1_Cells Cytolytic_Score IMPRES OS OS_time
1 1.2786746                         9.080701        11     0   732   
2 1.3304952                         9.106365        13     0  1174   
3 1.1829992                         6.875654         9     0   775   
4 1.1662425                         8.394944        11     0   695   
5 0.8444504                         3.958835         7     1    58   
6 1.0528275                         6.588683        10     0   891   
  Vincent_IPRES_NonResponder
1 6.504867                  
2 7.843231                  
3 7.105018                  
4 7.877998                  
5 7.114729                  
6 8.159180

# Fitting the Cox proportional model

In this notebook, we'll run an univariate Cox Proportional model and add a Benjamini–Hochberg procedure FDR.  

In [41]:
#helper function to organize a dataframe
create_ph_df <- function(coxphList, dataset){

  coef_stats <- as.data.frame(summary(coxphList)$conf.int)
  coef_stats$dataset <- dataset
  coef_stats$group <- row.names(coef_stats)
  coef_stats$pvalue <- (stats::coef(summary(coxphList))[,5])

  coef_stats %>%
    dplyr::mutate(logHR = log10(`exp(coef)`),
                  logupper = log10(`upper .95`),
                  loglower = log10(`lower .95`),
                  difflog=logHR-loglower,
                  logpvalue = -log10(pvalue))
}

# Running model for each dataset x feature combination
ph_df  <- purrr::map_dfr(.x = datasets, function(dataset){

    data_cox <- samples_pre %>%
        dplyr::filter(dataset_name == dataset)
    
    dataset_cox  <- purrr::map_dfr(.x = features, function(x){
     cox_features <- stats::as.formula(paste(
      "survival::Surv(OS_time, OS) ~ ", x))

    survival::coxph(cox_features, data_cox) %>%   
        create_ph_df(dataset = dataset) %>% 
        dplyr::mutate(FDR = p.adjust(pvalue, method = "BH"))%>%
        dplyr::mutate(heatmap_annotation = dplyr::case_when(
           is.na(FDR) ~ "",
           pvalue > 0.05 | FDR > 0.2 ~ "",
           pvalue <= 0.05 & FDR <= 0.2 & FDR > 0.05 ~ "*",
           pvalue <= 0.05 & FDR <= 0.05 ~ "**"
      ))
    })
    
  })

ph_df

exp(coef)  exp(-coef) lower .95  
IMPRES...1                             0.76747823  1.3029686 0.613917100
Vincent_IPRES_NonResponder...2         1.08201260  0.9242037 0.540111177
Cytolytic_Score...3                    0.70885878  1.4107182 0.588127623
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...4  0.14516257  6.8888281 0.014480882
IMPRES...5                             1.34977514  0.7408641 0.726049357
Vincent_IPRES_NonResponder...6         2.78732537  0.3587669 1.236639388
Cytolytic_Score...7                    1.32414858  0.7552023 0.862791478
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...8  0.04489180 22.2757830 0.001060605
IMPRES...9                             0.83973352  1.1908540 0.731158062
Vincent_IPRES_NonResponder...10        0.80977357  1.2349131 0.648972415
Cytolytic_Score...11                   0.93613589  1.0682210 0.837756607
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...12 0.08893972 11.2435703 0.019818787
IMPRES...13                            0.77832933  1.2848032 0.600164862
Vincent_IPRES_NonResponder...14        0.87017915  1.1491886 0.550393499
Cytolytic_Score...15                   0.89729800  1.1144570 0.773404830
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...16 0.14835500  6.7405883 0.020624165
IMPRES...17                            0.84171480  1.1880509 0.663060634
Vincent_IPRES_NonResponder...18        0.94167978  1.0619321 0.604258848
Cytolytic_Score...19                   0.81143711  1.2323814 0.702329868
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...20 0.11279926  8.8653063 0.031210867
                                       upper .95 dataset                
IMPRES...1                             0.9594501 Gide_Cell_2019         
Vincent_IPRES_NonResponder...2         2.1676116 Gide_Cell_2019         
Cytolytic_Score...3                    0.8543737 Gide_Cell_2019         
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...4  1.4551718 Gide_Cell_2019         
IMPRES...5                             2.5093238 HugoLo_IPRES_2016      
Vincent_IPRES_NonResponder...6         6.2824966 HugoLo_IPRES_2016      
Cytolytic_Score...7                    2.0322053 HugoLo_IPRES_2016      
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...8  1.9001167 HugoLo_IPRES_2016      
IMPRES...9                             0.9644322 Liu_NatMed_2019        
Vincent_IPRES_NonResponder...10        1.0104177 Liu_NatMed_2019        
Cytolytic_Score...11                   1.0460680 Liu_NatMed_2019        
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...12 0.3991301 Liu_NatMed_2019        
IMPRES...13                            1.0093836 Riaz_Nivolumab_2017    
Vincent_IPRES_NonResponder...14        1.3757644 Riaz_Nivolumab_2017    
Cytolytic_Score...15                   1.0410378 Riaz_Nivolumab_2017    
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...16 1.0671563 Riaz_Nivolumab_2017    
IMPRES...17                            1.0685053 VanAllen_antiCTLA4_2015
Vincent_IPRES_NonResponder...18        1.4675181 VanAllen_antiCTLA4_2015
Cytolytic_Score...19                   0.9374942 VanAllen_antiCTLA4_2015
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...20 0.4076680 VanAllen_antiCTLA4_2015
                                       group                            
IMPRES...1                             IMPRES                           
Vincent_IPRES_NonResponder...2         Vincent_IPRES_NonResponder       
Cytolytic_Score...3                    Cytolytic_Score                  
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...4  BIOCARTA_CTLA4_V_Bindea_Th1_Cells
IMPRES...5                             IMPRES                           
Vincent_IPRES_NonResponder...6         Vincent_IPRES_NonResponder       
Cytolytic_Score...7                    Cytolytic_Score                  
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...8  BIOCARTA_CTLA4_V_Bindea_Th1_Cells
IMPRES...9                             IMPRES                           
Vincent_IPRES_NonResponder...10        Vincent_IPRES_NonResponder       
Cytolytic_Score...11                   Cytolytic_Score                  
BIOCARTA_CTLA4_V_Bindea_Th1_Cells...12 BIOCARTA_CTLA4_V_Bindea_Th1_Cells
IMPRES...13             

# Visualization
    
Lastly, let's plot the results in a heatmap.

In [44]:
p  <- ph_df %>%
    dplyr::select(dataset, group, logHR) %>%
    tidyr::pivot_wider(names_from = group, values_from = logHR) %>%
    as.data.frame()

row.names(p) <- p$dataset
p$dataset <- NULL

plot_df  <- t(as.matrix(p))

plot  <- plotly::plot_ly(
        z = plot_df,
        x = colnames(plot_df),
        y = rownames(plot_df),
        type = "heatmap",
        colors = rev(RColorBrewer::brewer.pal(8, "RdBu"))
        ) %>%
    plotly::add_annotations(x = ph_df$dataset,
                    y = ph_df$group,
                    text = ph_df$heatmap_annotation,
                    showarrow = F,
                    font=list(color='black')) %>%
    plotly::add_annotations( text="BH pValue \n * <= 0.2 \n ** <= 0.05", xref="paper", yref="paper",
                     x=1.03, xanchor="left",
                     y=0, yanchor="bottom",
                     legendtitle=TRUE, showarrow=FALSE )

embed_notebook(plot)